In [1]:
import xlsxwriter

In [2]:
from repytex.tools.evaluation import Evaluation
import sqlite3

In [3]:
conn = sqlite3.connect('./recopytex.db')

In [4]:
ev = Evaluation.from_sqlite(16, conn)

In [5]:
ev.name

'DS4'

In [6]:
ev.ex_df

id                    name  eval_id                        date comment
0  43                   1 QCM       16  2018-01-16 00:00:00.000000        
1  44           2 Bien assis?       16  2018-01-16 00:00:00.000000        
2  45                3 L'urne       16  2018-01-16 00:00:00.000000        
3  46  4 Programme de calculs       16  2018-01-16 00:00:00.000000        
4  47        5 Roule cycliste       16  2018-01-16 00:00:00.000000        
5  51            Présentation       16  2018-01-17 00:00:00.000000

In [7]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

Formatages

In [8]:
eval_format = wb.add_format({'bold': True, 'font_color': 'red'})
eval_cell = wb.add_format()
eval_cell.set_bg_color("red")
# exo_cell

La feuille de calcul

In [9]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

In [10]:
ws = wb.add_worksheet()

En tête du tableau

In [11]:
ws.write(0,1,"Competence")
ws.write(0,2,"Barème")

0

Toutes les questions et exercices

In [12]:
def q_line(q, row, ws):
    ws.write(row, 0, f"{q.name} - {q.comment}")
    ws.write(row, 1, f"{q.competence}")
    ws.write(row, 2, q.score_rate)

In [13]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.write(row, 0, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+2, qrow+2)])
    for i in range(30):
        ws.write(row, i+2, f"=SUM({row_range})")
    return qrow

In [14]:
row = 2
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
ws.write(1,0, ev.name, eval_format)
exo_xls_range = ", ".join([f"C{i+1}" for i in exo_rows])
for i in range(30):
    ws.write(1,i+2, f"=SUM({exo_xls_range})", eval_format)

In [15]:
wb.close()

# Avec openpyxl

In [16]:
from openpyxl import Workbook
from openpyxl.styles import PatternFill, Border, Side, Alignment, Protection, Font, colors

In [17]:
colors.RED

'00FF0000'

In [18]:
wb = Workbook()

In [19]:
ws = wb.create_sheet(ev.name)

In [20]:
ws.cell(1,2,"Competence")
ws.cell(1,3,"Barème")

<Cell 'DS4'.C1>

In [21]:
def q_line(q, row, ws):
    ws.cell(row, 1, f"{q.name} - {q.comment}")
    ws.cell(row, 2, f"{q.competence}")
    ws.cell(row, 3, q.score_rate)

In [22]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.cell(row, 1, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+1, qrow+1)])
    ws.cell(row, 3, f"=SUM({row_range})")
    return qrow

In [23]:
row = 3
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
eval_row = ws.row_dimensions[2]
eval_row.fill = PatternFill(bgColor=colors.RED)
ws.cell(2,1, ev.name)
exo_xls_range = ", ".join([f"C{i}" for i in exo_rows])
ws.cell(2,3, f"=SUM({exo_xls_range})")

<Cell 'DS4'.C2>

In [24]:
wb.save("./DS4_302.xlsx")